# Overview

This notebook will show how to intergrate an LLM through Amazon SageMaker JumpStart into Amazon Redshift ML.

# Prerequisites

For this demo, you need to create
1. An Amazon Redshift Serverless preview workgroup or an Amazon Redshift provisioned preview cluster. Refer to creating a preview workgroup or creating a preview cluster documentation for steps
- [Serverless Preview](https://docs.aws.amazon.com/redshift/latest/mgmt/serverless-workgroup-preview.html)
- [Provisioned Preview](https://docs.aws.amazon.com/redshift/latest/mgmt/managing-clusters-console.html#cluster-preview)


2. LLM model and SageMaker endpoint.  Please follow the below instruction.  For further help, please refer this [blog](https://aws.amazon.com/blogs/big-data/large-language-models-for-sentiment-analysis-with-amazon-redshift-ml-preview/)

3. Download sample Amazon reviews dataset for Step 2B from S3 bucket - https://aws-blogs-artifacts-public.s3.amazonaws.com/BDB-3745/sample_reviews.csv

(This notebook will focus on falcon_7b_instruct_llm_model)

# 1. Setting up Amazon SageMaker with LLM and creating end point

A. Navigating from  Amazon SageMaker in your console, under JumpStart, select Foundation models. In this scenario, select falcon_7b_instruct_llm_model to open the notebook in Studio.
* If you do not have a domain and user, it will take a few minutes for the domain to be created.

B. When the notebook opens, a prompt "Set up notebook environment" pops up. For this demo, please select ml.m5.8xlarge as the instance recommended in the blog does not have quotas by default in your Isengard envrionment.

C. Scroll to the "Deploying Falcon Model for inference" section on the notebook and run the 3 cells in that section.

D. Once the third cell execution is complete, expand Deployments section in the left pane, choose Endpoints to see the endpoint created. You can see endpoint Name. Make a note of that. It will be used in the next steps.

# 2. Using Amazon Redshift Query Editor v2 for ML functionality

A. Using Amazon Redshift ML, create a model referencing the SageMaker JumpStart LLM endpoint

In [0]:
CREATE MODEL falcon_7b_instruct_llm_model
FUNCTION falcon_7b_instruct_llm_model(super)
RETURNS super
SAGEMAKER '<endpointname>'
IAM_ROLE default;

B. Upload sample Amazon reviews data set listed in the prerequisites into your S3 bucket and load data into your data warehouse

In [0]:
CREATE TABLE sample_reviews
(
    review varchar(4000)
);

COPY sample_reviews 
FROM 's3://sontitut/sample_reviews.csv'
IAM_ROLE DEFAULT
csv
DELIMITER ','
IGNOREHEADER 1;

C. Create a UDF that engineers the prompt for sentiment analysis

In [0]:
CREATE FUNCTION udf_prompt_eng_sentiment_analysis (varchar)
  returns super
stable
as $$
  select json_parse(
  '{"inputs":"Classify the sentiment of this sentence as Positive, Negative, Neutral. Return only the sentiment nothing else.' || $1 || '","parameters":{"max_new_tokens":1000}}')
$$ language sql;

D. Make a remote inference to the LLM model to generate sentiment analysis for input dataset

In [0]:
CREATE table sentiment_analysis_for_reviews
as
(
    SELECT 
        review, 
        falcon_7b_instruct_llm_model
            (
                udf_prompt_eng_sentiment_analysis(review)
        ) as sentiment
    from sample_reviews
);

E. Analyze the output with this query

In [0]:
SELECT review, sentiment[0]."generated_text" :: varchar as sentiment
FROM sentiment_analysis_for_reviews;

# 3. Clean Up

Ensure to stop any running SageMaker instances

Delete LLM endpoint in SageMaker

Drop samples_reviews table and model from Amazon Redshift using below query

And delete Redshift cluster after cleanup

In [0]:
DROP MODEL falcon_7b_instruct_llm_model;
DROP TABLE sample_reviews;
DROP FUNCTION fn_gen_prompt_4_sentiment_analysis;